In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 28,]

In [4]:
head(dat)

X   Date       Season round period home.name away.name home.score
145 163 2018-04-15 2018   4     27     GE        SK        103       
146 164 2018-04-15 2018   4     27     HW        ME        115       
147 165 2018-04-15 2018   4     27     ES        PA        106       
148 166 2018-04-14 2018   4     27     WC        GC        139       
149 167 2018-04-14 2018   4     27     NM        CA        116       
150 168 2018-04-14 2018   4     27     WB        SY         79       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
145 56         15         ... 1.9                  1.9                 
146 48         18         ... 1.9                  1.9                 
147 84         16         ... 1.9                  1.9                 
148 59         21         ... 1.9                  1.9                 
149 30         18         ... 1.9                  1.9                 
150 86         11         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
145 1.9                    1.9                    1.9                  
146 1.9                    1.9                    1.9                  
147 1.9                    1.9                    1.9                  
148 1.9                    1.9                    1.9                  
149 1.9                    1.9                    1.9                  
150 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
145 1.9                   1.9                            8          16         
146 1.9                   1.9                            9          11         
147 1.9                   1.9                            5           3         
148 1.9                   1.9                            2          17         
149 1.9                   1.9                           12           4         
150 1.9                   1.9                            6           7

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [5]:
matchup <- data[data$period == 28,]
n.matches <- length(matchup$home.number)
matchup

X   Date       Season round period home.name away.name home.score
136 154 2018-04-25 2018   5     28     CW        ES        101       
137 155 2018-04-24 2018   5     28     ME        RI         56       
138 156 2018-04-22 2018   5     28     BL        GC         71       
139 157 2018-04-22 2018   5     28     NM        HW         98       
140 158 2018-04-21 2018   5     28     FR        WB        108       
141 159 2018-04-21 2018   5     28     PA        GE         50       
142 160 2018-04-21 2018   5     28     CA        WC         69       
143 161 2018-04-21 2018   5     28     SK        GW         73       
144 162 2018-04-20 2018   5     28     SY        AD         75       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
136  52        14         ... 1.9                  1.9                 
137 102         8         ... 1.9                  1.9                 
138  76        10         ... 1.9                  1.9                 
139  70        14         ... 1.9                  1.9                 
140  54        16         ... 1.9                  1.9                 
141  84         7         ... 1.9                  1.9                 
142  79        10         ... 1.9                  1.9                 
143  73        10         ... 1.9                  1.9                 
144  85        10         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
136 1.9                    1.9                    1.9                  
137 1.9                    1.9                    1.9                  
138 1.9                    1.9                    1.9                  
139 1.9                    1.9                    1.9                  
140 1.9                    1.9                    1.9                  
141 1.9                    1.9                    1.9                  
142 1.9                    1.9                    1.9                  
143 1.9                    1.9                    1.9                  
144 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
136 1.9                   1.9                           10          16         
137 1.9                   1.9                           12          11         
138 1.9                   1.9                            9           6         
139 1.9                   1.9                           13          15         
140 1.9                   1.9                            7          14         
141 1.9                   1.9                            3           8         
142 1.9                   1.9                           17           5         
143 1.9                   1.9                            4           1         
144 1.9                   1.9                           18           2

# Data

In [6]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [7]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [8]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [9]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [10]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [11]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd    2.5%    25%    50%    75%
delta                      0.64    0.00   0.07    0.51   0.59   0.64   0.68
attackGoals_raw[1,1]       1.85    0.09   2.66   -3.41   0.06   1.80   3.79
attackGoals_raw[1,2]      -4.92    0.09   2.78   -8.92  -7.19  -5.20  -3.09
attackGoals_raw[1,3]      -3.42    0.11   3.22   -8.62  -5.89  -3.65  -1.27
attackGoals_raw[1,4]      -0.35    0.13   3.21   -7.05  -2.44  -0.22   1.83
attackGoals_raw[1,5]       0.55    0.12   2.69   -4.74  -1.24   0.57   2.41
attackGoals_raw[1,6]       0.99    0.09   2.82   -4.98  -0.82   1.03   2.95
attackGoals_raw[1,7]      -0.34    0.12   2.62   -5.33  -2.11  -0.37   1.45
attackGoals_raw[1,8]       1.19    0.11   2.81   -4.46  -0.69   1.17   2.98
attackGoals_raw[1,9]       1.37    0.07   1.92   -2.34

In [11]:
fit <- sflist2stanfit(sflist)

In [12]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     9.115592e-01 0.0011550956 6.851106e-02  7.745389e-01
attackGoals_raw[1,1]      1.868406e+00 0.0656146108 2.595516e+00 -3.167847e+00
attackGoals_raw[1,2]     -1.551489e+00 0.0579670099 3.200199e+00 -7.653858e+00
attackGoals_raw[1,3]      1.385508e+00 0.0645607663 2.972268e+00 -4.388288e+00
attackGoals_raw[1,4]     -2.275971e+00 0.0544867380 2.776994e+00 -7.401044e+00
attackGoals_raw[1,5]      1.218866e+00 0.0554022900 3.248551e+00 -5.374101e+00
attackGoals_raw[1,6]      9.554424e-01 0.0618602497 2.947829e+00 -4.669333e+00
attackGoals_raw[1,7]      1.186588e+00 0.0575459276 2.953252e+00 -4.514625e+00
attackGoals_raw[1,8]     -1.695372e-01 0.0498839635 2.740462e+00 -5.550823e+00
attackGoals_raw[1,9]     -2.906504e-02 0.0662152255 3.198975e+00 -6.356929e+00
attackGoals_raw[1,10]    -3.331950e+00 0.0586449989 3.306868e+00 -8.585258e+00
attackGoals_raw[1,11]     1.864850e+00 0.05

# Extract parameters

In [13]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [14]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [15]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [16]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [17]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [18]:
actual.total.diff
correct.vec

[1]  49 -46  -5  28  54 -34 -10   0 -10

[1] FALSE FALSE FALSE  TRUE  TRUE  TRUE  TRUE FALSE  TRUE

# Calculate percentage of win, loss and draw

In [19]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [20]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]   [,6]   [,7]   [,8]   [,9]  
      [1,] 0.4136 0.9322 0.8338 0.8106 0.6174 0.2704 0.2544 0.9022 0.1374
      [2,] 0.0388 0.0082 0.0162 0.0328 0.0674 0.0448 0.0254 0.0082 0.0192
      [3,] 0.5476 0.0596 0.1500 0.1566 0.3152 0.6848 0.7202 0.0896 0.8434

In [21]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [22]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [23]:
sim.pred.mat

[,1]                [,2]    [,3]    [,4]    [,5]    [,6]    [,7]    
 [1,] behind diff         -2.4734 -1.13   -2.6132 7.4878  -1.2806 3.3458  
 [2,] goal diff           0.0398  15.5222 9.5194  5.7054  2.969   -3.7644 
 [3,] total diff          -2.2346 92.0032 54.5032 41.7202 16.5334 -19.2406
 [4,] home team           CW      ME      BL      NM      FR      PA      
 [5,] away team           ES      RI      GC      HW      WB      GE      
 [6,] actual result       49      -46     -5      28      54      -34     
 [7,] prediction correct? FALSE   FALSE   FALSE   TRUE    TRUE    TRUE    
 [8,] home win prob       0.4136  0.9322  0.8338  0.8106  0.6174  0.2704  
 [9,] draw prob           0.0388  0.0082  0.0162  0.0328  0.0674  0.0448  
[10,] home loss prob      0.5476  0.0596  0.15    0.1566  0.3152  0.6848  
[11,] simulated sd ests   32.4    153.44  100.39  80.65   50.42   45.31   
      [,8]     [,9]     [,10]   
 [1,] 0.2834   4.6296   -2.4178 
 [2,] -5.6712  19.0682  -7.2836 
 [3,] -33.7438 119.0388 -46.1194
 [4,] CA       SK       SY      
 [5,] WC       GW       AD      
 [6,] -10      0        -10     
 [7,] TRUE     FALSE    TRUE    
 [8,] 0.2544   0.9022   0.1374  
 [9,] 0.0254   0.0082   0.0192  
[10,] 0.7202   0.0896   0.8434  
[11,] 86.13    216.18   75.78

In [24]:
write.csv(t(sim.pred.mat),  file = "round5_prediction.csv")